# Is-albedo-tilbakekoblilngen
Seminar 3 i FYS1035, høsten 2022. Anja Røyne, UiO

**Start med å kjøre cella under for å importere pakkene vi trenger.**

In [ ]:
from numpy import *
from pylab import *

Når det er mye is på bakken og havene, er jordas albedo høy, som virker avkjølende og fremmer tilvekst av mer is. Og når mye av isen smelter, blir albedo lavere, som virker oppvarmende og gjør at mer is smelter. Nå skal vi prøve  lage en enkel modell for å gjenskape denne tilbakekoblingen. 

Vi kan gjøre det ved å la albedo avhenge av temperatur på denne måten ([hentet herfra](https://brian-rose.github.io/ClimateLaboratoryBook/courseware/assignment-zero-dim-ebm.html)):

$$ a(T) = \left\{ \begin{array}{ccc}
a_i &   & T \le T_i \\
a_o + (a_i-a_o) \frac{(T-T_o)^2}{(T_i-T_o)^2} &   & T_i < T < T_o \\
a_o &   & T \ge T_o \end{array} \right\}$$

med følgende verdier av parameterne:

- $a_o = 0.289$ albedo for varm, isfri planet
- $a_i = 0.7$ albedo for kald, isdekket planet
- $T_o = 293$ K, over denne temperaturen er planeten isfri
- $T_i = 260$ K, under denne temperaturen er planeten isdekket 

I cella under plotter vi $a$ som funksjon av $T$:

In [ ]:
# fysiske parametere
a_o = 0.289
a_i = 0.7
T_o = 293
T_i = 260
# variabler
T_c = linspace(-20,30,100) # liste over temperaturer i celcius
T = T_c + 273.15 # temperaturer i Kelvin
a_T = zeros(len(T)) # liste over albedo
# løkke for temperaturer
for i in range(len(T)):
    if T[i] < T_i:
        a_T[i] = a_i
    elif T[i] > T_o:
        a_T[i] = a_o
    else:
        a_T[i] = a_o+(a_i-a_o)*(T[i]-T_o)**2/(T_i-T_o)**2
plot(T_c,a_T)
xlabel("bakketemperatur (grader celcius)")
ylabel("albedo")

Nå kan vi sette denne modellen for albedo inn i klimamodellen vår og kjøre den. 

In [ ]:
# fysiske verdier:
S = 342 # W/m2, innstråling
sigma = 5.67e-8 # J/m2K, Stefan-Boltzmann-konstanten
epsilon = 0.6 # sett inn verdi for atmosfærens emissivitet
c_j = 4.0e8 # J/m2K, varmekapasitet for jorda
c_a = 1.02e7 # J/m2K, varmekapasitet for atmosfæren
T0j_c = 10 #grader celcius, starttemperatur for jordoverflaten
T0a_c = 2 #grader celcius, starttemperatur for atmosfæren
# parametere i albedo-modell:
a_o = 0.289
a_i = 0.7
T_o = 293
T_i = 260

# regner om starttemperaturene til kelvin:
T0j = T0j_c + 273.15
T0a = T0a_c + 273.15
# numeriske verdier:
N = 500 # antall tidssteg
dt = 0.05*365*24*3600 # antall sekunder per tidssteg (antall år * dager pr år * timer pr dag * sekunder pr time)

# lager en liste over alle tidspunktene: 
t = arange(1,N+1,1) 
# lager en tom liste der jeg skal lagre temperaturene for hvert år:
Tj = zeros(N)
Ta = zeros(N)

# tidsløkka:
for i in t: # dette skal gjøres for hver verdi av "t" etter tur, til lista er tom
    # alt som hører inne i løkka skal være flyttet ett hakk inn til høyre.
    if i == 1: # to likhetstegn brukes for å sjekke om i er akkurat lik 1
        Tj[i-1] = T0j 
        Ta[i-1] = T0a 
        # Python teller plassene i lister fra 0. Her sier jeg at i år 1 skal jeg legge startverdien på plass 0 i temperatur-lista
    else: # hvis vi ikke er i første år
        # atmosfærens utstråling
        Q_ut_a = 2*epsilon*sigma*Ta[i-2]**4
        # innstråling på jorda
        # må først finne albedo
        if Tj[i-2] < T_i:
            a = a_i
        elif Tj[i-2] > T_o:
            a = a_o
        else:
            a = a_o+(a_i-a_o)*(Tj[i-2]-T_o)**2/(T_i-T_o)**2
        Q_inn_j = (1-a)*S+1/2*Q_ut_a
        # utstråling fra jorda
        Q_ut_j = sigma*Tj[i-2]**4
        # temperatur, jorda
        Tj[i-1] = Tj[i-2]+ 1/c_j*(Q_inn_j-Q_ut_j)*dt # oppdaterer temperaturen basert på energibalansen
        # temperatur, atmosfæren
        Q_inn_a = epsilon*Q_ut_j
        Ta[i-1] = Ta[i-2]+ 1/c_a*(Q_inn_a-Q_ut_a)*dt # oppdaterer temperaturen basert på energibalansen
                
# tilbake til celcius
Tj_c = Tj-273.15
        
# plotte resultatet:
plot(t*dt/(365*24*3600),Tj_c)
xlabel("tid (år)")
ylabel("bakketemperatur (grader celcius)")

# hva blir sluttresultatet
print("Etter",format(t[-1]*dt/(365*24*3600),".2f"),"år er temperaturen blitt",format(Tj_c[-1],".2f"),"grader celcius.") 

**Blir resultatene annerledes enn i forrige modell? Hvordan? Hva skjer dersom du endrer på $\epsilon$? Hva kan du gjøre for å ende opp i en verden med lav eller høy albedo?**

## Ferdig?

Det ligger flere gode oppgaver under Assignments på denne siden: https://brian-rose.github.io/ClimateLaboratoryBook/home.html

